In [1]:
import os
os.listdir('../../scripts')
import sys
sys.path.append('../../Scripts')

In [2]:
from generate_signals import SignalGenerator
from preprocess_daily import DailyPreprocessor

In [3]:
inter_no = 175
Node_id = 'i0'

In [4]:
# desired result
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()
self.make_histids()
self.set_timepoints()
self.assign_red_yellow()
self.SIGTABLE

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.
4. 통합 테이블을 생성합니다.


inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704416690       1       1       8       4        33   
1         178     c30  1704416690       1       1       8       4         4   
2         178     c30  1704416690       2       2       7       3         1   
0         178     c30  1704416690       2       2       7       3        34   
1         178     c30  1704416690       2       2       7       3         4   
..        ...     ...         ...     ...     ...     ...     ...       ...   
2         210     u60  1704417140       3       3       7       4         1   
0         210     u60  1704417140       3       3       7       4        65   
1         210     u60  1704417140       3       3       7       4         4   
2         210     u60  1704417140       4       4       8       3         1   
237       210     u60  1704417140       4       4       8       3        19   

         state phase_sumo  
0       gggggg        0_g  
1       gggggg        0_y  
2       gggggg       1__r  
0       GGGGGG        1_g  
1       GGGGGG        1_y  
..         ...        ...  
2    ggggggggr       3__r  
0    ggggggggr        3_g  
1    ggggggggr        3_y  
2    ggggggggr       4__r  
237  ggggggggr        4_g  

[684 rows x 10 columns]

In [5]:
self = SignalGenerator()
self.prepare_data()
self.process_history()
self.process_movement()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.


In [6]:
self.merge_dfs()

In [7]:
# 4-2. histid
self.histid = self.movedur.copy()
self.histid['node_id'] = self.histid['inter_no'].map(self.inter2node)
histid_start = self.present_time - 600
self.histid = self.histid[self.histid.start_unix > histid_start]

mapping_dict = self.matching.set_index(['node_id', 'move_no'])['state'].to_dict()

for i, row in self.histid.iterrows():
    node_id = row.node_id
    move_A = row.move_A
    move_B = row.move_B
    
    # A링의 state 지정
    if (node_id, move_A) in mapping_dict:
        state_A = mapping_dict[(node_id, move_A)]
    else:
        state_A = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_A'] = state_A

    # B링의 state 지정
    if (node_id, move_B) in mapping_dict:
        state_B = mapping_dict[(node_id, move_B)]
    else:
        state_B = ''.join(self.node2init[node_id])
    self.histid.at[i, 'state_B'] = state_B    

In [8]:
self.histid

inter_no  start_unix  phas_A  phas_B  move_A  move_B  duration node_id  \
10        175  1704416540       1       1       8       4        43      i0   
11        175  1704416540       2       2       7       3        46      i0   
12        175  1704416540       3       3       6       1        33      i0   
13        175  1704416540       3       4       6       2        23      i0   
14        175  1704416540       4       4       5       2        37      i0   
..        ...         ...     ...     ...     ...     ...       ...     ...   
255       201  1704417410       1       1       8       3        33      i8   
256       201  1704417410       2       2       5       2        36      i8   
257       201  1704417410       3       3       6       2        25      i8   
258       201  1704417410       4       4       6       1        58      i8   
259       201  1704417410       5       5       7       4        18      i8   

               state_A            state_B  
10   grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
11   grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
12   grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
13   grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
14   grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
..                 ...                ...  
255   grrrrrrrgGGrgrrr   grrrrrrrgrrGgrrr  
256   grrrrrrrgrrrgrrG   grrrrrrrgrrrgGGr  
257   grrrGGGrgrrrgrrr   grrrrrrrgrrrgGGr  
258   grrrGGGrgrrrgrrr   grrrrrrGgrrrgrrr  
259   grrGrrrrgrrrgrrr   gGGrrrrrgrrrgrrr  

[203 rows x 10 columns]

In [16]:
# 4-3. histids
new_histids = []
for parent_id in self.parent_ids:
    for child_id in self.pa2ch[parent_id]:
        new_histid = self.histid.copy()[self.histid.node_id==parent_id].drop(columns=['state_A', 'state_B'])
        # new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = self.match6[self.match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]

            # A링의 state 지정
            state_A = Arow.iloc[0].state
            new_histid.at[i, 'state_A'] = state_A

            # B링의 state 지정
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            state_B = Brow.iloc[0].state
            new_histid.at[i, 'state_B'] = state_B

            new_histid.at[i, 'node_id'] = child_id
        new_histids.append(new_histid)
import pandas as pd
new_histids = pd.concat(new_histids)
self.histids = pd.concat([self.histid.copy(), new_histids])
self.histids = self.histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
self.histids = self.histids[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration', 'state_A', 'state_B']]
self.histids.query('node_id==@Node_id')

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
44        175      i0  1704416540       1       1       8       4        43   
45        175      i0  1704416540       2       2       7       3        46   
46        175      i0  1704416540       3       3       6       1        33   
47        175      i0  1704416540       3       4       6       2        23   
48        175      i0  1704416540       4       4       5       2        37   
109       175      i0  1704416720       1       1       8       4        43   
110       175      i0  1704416720       2       2       7       3        45   
111       175      i0  1704416720       3       3       6       1        33   
112       175      i0  1704416720       3       4       6       2        22   
113       175      i0  1704416720       4       4       5       2        37   
173       175      i0  1704416900       1       1       8       4        43   
174       175      i0  1704416900       2       2       7       3        45   
175       175      i0  1704416900       3       3       6       1        33   
176       175      i0  1704416900       3       4       6       2        22   
177       175      i0  1704416900       4       4       5       2        37   
244       175      i0  1704417080       1       1       8       4        43   
245       175      i0  1704417080       2       2       7       3        45   
246       175      i0  1704417080       3       3       6       1        33   
247       175      i0  1704417080       3       4       6       2        22   
248       175      i0  1704417080       4       4       5       2        37   
306       175      i0  1704417260       1       1       8       4        43   
307       175      i0  1704417260       2       2       7       3        45   
308       175      i0  1704417260       3       3       6       1        33   
309       175      i0  1704417260       3       4       6       2        22   
310       175      i0  1704417260       4       4       5       2        37   
357       175      i0  1704417420       1       1       8       4        38   
358       175      i0  1704417420       2       2       7       3        40   
359       175      i0  1704417420       3       3       6       1        29   
360       175      i0  1704417420       3       4       6       2        20   
361       175      i0  1704417420       4       4       5       2        33   

               state_A            state_B  
44   grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
45   grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
46   grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
47   grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
48   grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
109  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
110  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
111  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
112  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
113  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
173  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
174  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
175  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
176  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
177  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
244  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
245  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
246  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
247  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
248  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
306  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
307  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
308  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
309  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
310  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr  
357  grrrgrrrgGGGGrgrr  gGGrgrrrgrrrrrgrr  
358  grrGgrrrgrrrrrgrr  grrrgrrrgrrrrGgrr  
359  grrrgGGrgrrrrrgrr  grrrgrrGgrrrrrgrr  
360  grrrgGGrgrrrrrgrr  grrrgrrrgrrrrrgGr  
361  grrrgrrrgrrrrrgrG  grrrgrrrgrrrrrgGr

In [9]:
self.set_timepoints()

In [12]:
self.sigtable

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         178     c30  1704418730       1       1       8       4        38   
1         178     c30  1704418730       2       2       7       3        39   
2         178     c30  1704418730       3       3       5       2        43   
3         178     c30  1704418730       4       4       6       1        22   
4         178     c30  1704418900       1       1       8       4        38   
..        ...     ...         ...     ...     ...     ...     ...       ...   
233       210     u60  1704419299       1       1       6      18        28   
234       210     u60  1704419299       1       2       6       2        15   
235       210     u60  1704419299       2       2       5       2        43   
236       210     u60  1704419299       3       3       7       4        70   
237       210     u60  1704419299       4       4       8       3        24   

       state_A    state_B  phase_sumo  
0       gggggg     gggggg           0  
1       GGGggg     gggGGG           1  
2       GGGggg     gggGGG           2  
3       GGGggg     gggGGG           3  
4       gggggg     gggggg           0  
..         ...        ...         ...  
233  ggggggggr  ggggggggr           0  
234  ggggggggr  ggggggggr           1  
235  ggggggggG  ggggggggr           2  
236  ggggggggr  ggggggggr           3  
237  ggggggggr  ggggggggr           4  

[238 rows x 11 columns]

In [73]:
# 5-2-1 helper function of 5-2
def get_red(pre_state:str, cur_state:str):
    assert len(pre_state) == len(cur_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_r = ''
    for c, n in zip(pre_state, cur_state):
        if c == n:
            state_r += c
        elif (c == 'r') and (n == 'G'):
            state_r += 'r'
        elif (c == 'G') and (n == 'r'):
            state_r += 'r'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_r

# 5-2-2 helper function of 5-2
def get_yellow(cur_state:str, nex_state:str):
    assert len(cur_state) == len(nex_state), "cur_state, nex_state의 길이가 서로 다릅니다."
    state_y = ''
    for c, n in zip(cur_state, nex_state):
        if c == n:
            state_y += c
        elif (c == 'r') and (n == 'G'):
            state_y += 'r'
        elif (c == 'G') and (n == 'r'):
            state_y += 'y'
        else:
            raise ValueError(f"예상치 못한 신호조합: current={c}, next={n}")
    return state_y

# 5-2-3 helper function of 5-2
def cumulate(sig, alph):
    csig = [] # cumulated sig
    pre = pd.Series({f'phas_{alph}':None})

    start_time = 0
    elapsed = 0
    for i, cur in sig.iterrows():
        start_unix = cur.start_unix
        
        # pre, nex
        if i != 0:
            pre = sig.iloc[i-1]
        
        if i != len(sig) - 1:
            nex = sig.iloc[i+1]
        
        # duration
        if cur[f'phas_{alph}'] == nex[f'phas_{alph}']:
            continue
        if cur[f'phas_{alph}'] == pre[f'phas_{alph}']:
            duration = cur.duration + pre.duration
        else:
            duration = cur.duration
        start_times = []
        states = []
        phases = []

        # red
        if i != 0:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_red(pre[f'state_{alph}'], cur[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}r')

            elapsed = cur[f'red_{alph}']

        # green
        if i == 0:
            start_time = 0
        else:
            start_time += elapsed
        start_times.append(start_time)
        states.append(cur[f'state_{alph}'])
        phases.append(f'{cur[f"phas_{alph}"]}g')
        if i == 0:
            elapsed = duration - cur[f'yellow_{alph}']
        else:
            elapsed = duration - cur[f'yellow_{alph}'] - cur[f'red_{alph}']

        # yellow
        if i != len(sig) - 1:
            start_time += elapsed
            start_times.append(start_time)
            states.append(get_yellow(cur[f'state_{alph}'], nex[f'state_{alph}']))
            phases.append(f'{cur[f"phas_{alph}"]}y')
            elapsed = cur[f'yellow_{alph}']
        sig_ = pd.DataFrame({'start_time':start_times, f'phas_{alph}':phases, f'state_{alph}':states})
        sig_['start_unix'] = start_unix
        csig.append(sig_)
    csig = pd.concat(csig).reset_index(drop=True)
    return csig

In [89]:
import time
now = time.time()
self.SIGTABLE = []
for node_id in self.sigtable.node_id.unique():
    sig = self.sigtable.query('node_id==@node_id')
    for i, row in sig.iterrows():
        inter_no = row.inter_no
        phas_A = row.phas_A
        phas_B = row.phas_B
        start_unix = row.start_unix
        prow = self.load_prow(inter_no, start_unix)[1].iloc[0]
        red_A    = prow[f'red_A{phas_A}']
        yellow_A = prow[f'yellow_A{phas_A}']
        red_B    = prow[f'red_B{phas_B}']
        yellow_B = prow[f'yellow_B{phas_B}']
        sig.loc[i, ['red_A', 'red_B', 'yellow_A', 'yellow_B']] = red_A, red_B, yellow_A, yellow_B
    sig = sig.astype({'red_A': int, 'red_B': int, 'yellow_A': int, 'yellow_B': int,
                    'phas_A':str, 'phas_B':str})
    sig = sig.drop(['move_A','move_B'], axis=1)

    sig_A = sig[['start_unix', 'phas_A', 'duration', 'state_A', 'red_A', 'yellow_A']].reset_index(drop=True)
    sig_B = sig[['start_unix', 'phas_B', 'duration', 'state_B', 'red_B', 'yellow_B']].reset_index(drop=True)

    csig_A = cumulate(sig_A, 'A')
    csig_B = cumulate(sig_B, 'B')

    SIG = pd.merge(csig_A, csig_B, on=['start_time', 'start_unix'], how='outer')
    SIG = SIG.sort_values(by='start_time').reset_index(drop=True)
    SIG[['phas_A', 'state_A']] = SIG[['phas_A', 'state_A']].fillna(method='ffill')
    SIG[['phas_B', 'state_B']] = SIG[['phas_B', 'state_B']].fillna(method='ffill')
    SIG['phase'] = SIG['phas_A'] + "_" + SIG['phas_B']
    SIG['node_id'] = node_id
    SIG = SIG[['node_id', 'start_unix', 'start_time', 'phase', 'state_A', 'state_B']]
    SIG['duration'] = SIG['start_time'].shift(-1) - SIG['start_time']
    SIG = SIG[:-1]
    SIG['duration'] = SIG['duration'].astype(int)
    for row in SIG.itertuples():
        state = ''
        for a, b, in zip(row.state_A, row.state_B):
            if a == 'r':
                state += b
            elif b == 'r':
                state += a
            elif a == b:
                state += a
            else:
                raise ValueError(f"예상되지 않은 조합 발생: a={a}, b={b}")
        SIG.at[row.Index, 'state'] = state
    SIG = SIG.drop(columns=['start_time', 'state_A', 'state_B'])
    self.SIGTABLE.append(SIG)
self.SIGTABLE = pd.concat(self.SIGTABLE)
self.SIGTABLE
print(time.time() - now)

0.6227824687957764


In [46]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:14<00:00, 1200.17it/s]


2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [97]:
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:15<00:00, 1135.80it/s]


In [99]:
self.get_matches()

이동류정보 불러오는 중:   0%|          | 0/17280 [00:00<?, ?it/s]

이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1274.30it/s]


2-1. 매칭 테이블들을 생성했습니다.


In [104]:
self.initialize_state()

2-2. 비보호우회전(g)을 배정했습니다.


In [142]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 연등교차로
for _, row in self.coord.iterrows():
    node_id = row.node_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if not (pd.isna(inc_edge) and pd.isna(out_edge)):
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 유턴교차로
for _, row in self.uturn.iterrows():
    node_id = row.child_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if not (pd.isna(inc_edge) and pd.isna(out_edge)):
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

self.node2init['u00']

['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g', 'g']

In [135]:
self.uturn

parent_id child_id direction condition         inc_edge         out_edge
0        i0      u00         북      좌회전시     571500487_02  571500487_01.32
1        i2      u20         북     보행신호시  571542810_01.51     571542810_02
2        i3      u30         북     보행신호시     571556452_01     571556452_02
3        i3      u31         동     보행신호시     571500475_02  571500475_01.26
4        i3      u32         서     보행신호시     571540303_02    -571540303_02
5        i6      u60         서      좌회전시     571500535_02    -571500535_02

In [108]:
self.node2init

{'c30': ['g', 'g', 'g', 'g', 'g', 'g'],
 'i0': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r'],
 'i1': ['g', 'r', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r'],
 'i2': ['r', 'r', 'g', 'r', 'r', 'r', 'r'],
 'i3': ['g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r'],
 'i6': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i7': ['r', 'r', 'r', 'g', 'g', 'r', 'r'],
 'i8': ['g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i9': ['r', 'r', 'r', 'r'],
 'u00': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g', 'g'],
 'u20': ['g', 'g', 'g', 'g', 'g', 'g'],
 'u30': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g'],
 'u31': ['g', 'g', 'g', 'g', 'r', 'g', 'g', 'g'],
 'u32': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'r'],
 'u60': ['g', 'g', 'g', 'g',

In [62]:
self.node2inter = dict(zip(self.inter_node['node_id'], self.inter_node['inter_no']))

self.parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
self.child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())
self.uturn_ids = sorted(self.uturn.child_id.unique())
self.coord_ids = sorted(self.coord.child_id.unique())

ch2pa = {} # child to parent
for child_id in self.child_ids:
    parent_no = self.inter_node[self.inter_node.node_id==child_id].inter_no.iloc[0]
    sub_inter_node = self.inter_node[self.inter_node.inter_no==parent_no]
    ch2pa[child_id] = sub_inter_node[sub_inter_node.inter_type=='parent'].iloc[0].node_id
directions = ['북', '북동', '동', '남동', '남', '남서', '서', '북서'] # 정북기준 시계방향으로 8방향


In [64]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    direction = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge
    out_edge_id = row.out_edge
    # match5에서 parent_id에 해당하는 행들을 가져옴
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge', 'out_edge']] = np.nan

    # condition 별로 inc_dire, out_dire_A, out_dire_B를 정함
    ind = directions.index(direction)
    if condition == "좌회전시":
        inc_dire = direction
        out_dire_A = out_dire_B = directions[(ind + 2) % len(directions)]
    elif condition == "보행신호시":
        inc_dire = directions[(ind + 2) % len(directions)]
        out_dire_A = directions[(ind - 2) % len(directions)]
        out_dire_B = directions[(ind - 2) % len(directions)]

    # (inc_dire, out_dire_A, out_dire_B) 별로 inc_edge_id, out_edge_id를 정함
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    if condition == '보행신호시':
        # 이동류번호가 17(보행신호)이면서 유턴노드방향으로 가는 신호가 없으면 (inc_edge_id, out_edge_id)를 부여한다.
        cmatch.loc[(cmatch.move_no==17) & (cmatch.out_dir!=direction), ['inc_edge', 'out_edge']] = [inc_edge_id, out_edge_id]
    # 유턴신호의 이동류번호를 19로 부여한다.
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_A), 'move_no'] = 19
    cmatch.loc[(cmatch.inc_dir==inc_dire) & (cmatch.out_dir==out_dire_B), 'move_no'] = 19
    cmatches.append(cmatch)


In [63]:
import numpy as np
# 각 coordination node에 대하여 (inc_edge_id, out_edge_id) 부여
self.coord['inter_no'] = self.coord['parent_id'].map(self.node2inter)
self.coord = self.coord.rename(columns={'child_id':'node_id'})
self.coord[['inc_dir', 'out_dir', 'inc_angle','out_angle']] = np.nan
self.coord['move_no'] = 20
self.coord = self.coord[['inter_no', 'phase_no', 'ring_type', 'move_no', 'inc_dir', 'out_dir', 'inc_angle','out_angle', 'inc_edge', 'out_edge', 'node_id']]
self.coord

inter_no  phase_no ring_type  move_no  inc_dir  out_dir  inc_angle  \
0       178         1         A       20      NaN      NaN        NaN   
1       178         1         B       20      NaN      NaN        NaN   
2       178         2         A       20      NaN      NaN        NaN   
3       178         2         B       20      NaN      NaN        NaN   
4       178         3         A       20      NaN      NaN        NaN   
5       178         3         B       20      NaN      NaN        NaN   
6       178         4         A       20      NaN      NaN        NaN   
7       178         4         B       20      NaN      NaN        NaN   

   out_angle         inc_edge          out_edge node_id  
0        NaN              NaN               NaN     c30  
1        NaN              NaN               NaN     c30  
2        NaN     571542116_01  -571542116_02.96     c30  
3        NaN  571542116_02.96  571542116_02.164     c30  
4        NaN     571542116_01  -571542116_02.96     c30  
5        NaN  571542116_02.96  571542116_02.164     c30  
6        NaN     571542116_01  -571542116_02.96     c30  
7        NaN  571542116_02.96  571542116_02.164     c30

In [65]:
# display(coord)
cmatches = pd.concat(cmatches)
self.match6 = pd.concat([self.match5, cmatches, self.coord]).drop_duplicates().sort_values(by=['inter_no', 'node_id', 'phase_no', 'ring_type'])
# self.match6.to_csv(os.path.join(self.path_intermediates, 'match6.csv'))


In [94]:
self.node2init

{'c30': ['g', 'g', 'g', 'g', 'g', 'g'],
 'i0': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r'],
 'i1': ['g', 'r', 'r', 'g', 'g', 'g', 'r', 'g', 'r', 'r'],
 'i2': ['g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'i3': ['g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r'],
 'i6': ['g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i7': ['g', 'g', 'r', 'g', 'g', 'r', 'r'],
 'i8': ['g',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r',
  'g',
  'r',
  'r',
  'r'],
 'i9': ['g', 'g', 'g', 'g'],
 'u00': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u20': ['g', 'g', 'g', 'g', 'g', 'g'],
 'u30': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u31': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u32': ['g', 'g', 'g', 'g', 'g', 'g', 'g', 'g'],
 'u60': ['g', 'g', 'g', 'g',

In [95]:
self.node2init = {}
node_id = 'c30'
node = self.net.getNode(node_id)

node_id = node.getID()
# 모든 connection
conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
conns = [c for c in conns if c[0] >= 0]
conns = sorted(conns, key=lambda x: x[0])
state = []
# i번째 connection : ci
for i, ci in conns:
    if ci.getTLLinkIndex() < 0:
        continue
    are_foes = False
    # j번째 connection : cj
    # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
    # 그외의 경우에는 are_foes = False (g)
    for j, cj in conns:
        # ci, cj의 합류지점이 같으면 통과
        if ci.getTo() == cj.getTo():
            continue
        # ci, cj가 상충되면 are_foes를 True로 지정.
        if node.areFoes(i, j):
            are_foes = True
            break
    state.append('r' if are_foes else 'g')
self.node2init[node_id] = state

In [96]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

# 연등교차로에도 마찬가지로 신호가 부여되어 있는 경우에 r 부여
for _, row in self.coord.iterrows():
    node_id = row.node_id
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    inc_edge = self.net.getEdge(inc_edge)
    out_edge = self.net.getEdge(out_edge)
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            self.node2init[node_id][index] = 'r'


# json 파일로 저장
with open(os.path.join(self.path_intermediates, 'node2init.json'), 'w') as file:
    json.dump(self.node2init, file)


AttributeError: 'Series' object has no attribute 'inc_edge'

In [48]:
import copy
# assign signals on matching
self.matching['init_state'] = self.matching['node_id'].map(self.node2init)
self.matching['state'] = self.matching['init_state'].map(lambda x:''.join(x))
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'state']]

# assign signals on match6

self.match6 = self.match6.reset_index(drop=True)
self.match6['init_state'] = self.match6['node_id'].map(self.node2init)
self.match6['state'] = self.match6['init_state'].map(lambda x:''.join(x))

# match6의 각 행을 순회
for i, row in self.match6.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]
    if (pd.isna(inc_edge)) or (pd.isna(out_edge)):
        continue
    if (move_no != 21):
        # print(i, node_id, move_no, ''.join(state))
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
            # print(i, node_id, move_no, index, ''.join(state))
        self.match6.at[i, 'state'] = ''.join(state)

self.match6 = self.match6.dropna(subset='state')
self.match6 = self.match6.reset_index(drop=True)
self.match6 = self.match6[['inter_no', 'node_id', 'phase_no', 'ring_type', 'move_no', 'state']]
self.match6

AttributeError: 'Pandas' object has no attribute 'inc_edge'

In [146]:
node_id = 'i2'
node = self.net.getNode(node_id)
self.node2init = {}
# 모든 connection
conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
conns = [c for c in conns if c[0] >= 0]
conns = sorted(conns, key=lambda x: x[0])
state = []
# i번째 connection : ci
for i, ci in conns:
    if ci.getTLLinkIndex() < 0:
        continue
    are_foes = False
    # j번째 connection : cj
    # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
    # 그외의 경우에는 are_foes = False (g)
    for j, cj in conns:
        # ci, cj의 합류지점이 같으면 통과
        if ci.getTo() == cj.getTo():
            continue
        # ci, cj가 상충되면 are_foes를 True로 지정.
        if node.areFoes(i, j):
            are_foes = True
            break
    state.append('r' if are_foes else 'g')
self.node2init[node_id] = state
print(state)

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

['g', 'g', 'g', 'g', 'g', 'g', 'g']


KeyError: 'i0'

In [161]:
self.match4[self.match4.inter_no==177]

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
14       177         1         A        8       남       북       180       000
15       177         1         B        4       북       남       001       176
16       177         2         A        7       북       동       000       090
17       177         2         B        3       남       서       179       270
18       177         3         A       17     NaN     NaN       NaN       NaN
19       177         3         B       18     NaN     NaN       NaN       NaN
20       177         4         A        5       서       북       268       000
21       177         4         B        1       동       남       090       180

In [160]:

self.match5[self.match5.node_id=='i2']

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
14       177         1         A        8       남       북       180       000   
15       177         1         B        4       북       남       001       176   
16       177         2         A        7       북       동       000       090   
17       177         2         B        3       남       서       179       270   
18       177         3         A       17     NaN     NaN       NaN       NaN   
19       177         3         B       18     NaN     NaN       NaN       NaN   
20       177         4         A        5       서       북       268       000   
21       177         4         B        1       동       남       090       180   

         inc_edge      out_edge node_id  
14  -571542809_01  571542811_01      i2  
15   571542811_02  571542809_01      i2  
16   571542811_02  571542107_01      i2  
17  -571542809_01  571542809_01      i2  
18            NaN           NaN      i2  
19            NaN           NaN      i2  
20  -571542809_01  571542811_01      i2  
21   571542107_02  571542809_01      i2

In [151]:
self.match5[self.match5.node_id=='i2']

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
14       177         1         A        8       남       북       180       000   
15       177         1         B        4       북       남       001       176   
16       177         2         A        7       북       동       000       090   
17       177         2         B        3       남       서       179       270   
18       177         3         A       17     NaN     NaN       NaN       NaN   
19       177         3         B       18     NaN     NaN       NaN       NaN   
20       177         4         A        5       서       북       268       000   
21       177         4         B        1       동       남       090       180   

         inc_edge      out_edge node_id  
14  -571542809_01  571542811_01      i2  
15   571542811_02  571542809_01      i2  
16   571542811_02  571542107_01      i2  
17  -571542809_01  571542809_01      i2  
18            NaN           NaN      i2  
19            NaN           NaN      i2  
20  -571542809_01  571542811_01      i2  
21   571542107_02  571542809_01      i2

In [148]:
self.matching[self.matching.node_id=='i2']

inter_no  move_no inc_dir out_dir       inc_edge      out_edge node_id
19       177        1       동       남   571542107_02  571542809_01      i2
20       177        2       서       동  -571542809_01  571542107_01      i2
21       177        3       남       서  -571542809_01  571542809_01      i2
22       177        4       북       남   571542811_02  571542809_01      i2
23       177        5       서       북  -571542809_01  571542811_01      i2
24       177        6       동       서   571542107_02  571542809_01      i2
25       177        7       북       동   571542811_02  571542107_01      i2
26       177        8       남       북  -571542809_01  571542811_01      i2
27       177       21       북       서   571542811_02  571542809_01      i2
28       177       21       서       남  -571542809_01  571542809_01      i2
29       177       21       남       동  -571542809_01  571542107_01      i2
30       177       21       동       북   571542107_02  571542811_01      i2